# AlphaViz tutorial

This tutorial covers the basics of using AlphaViz as a Python package. It includes the following sections:
1. [**Setup**](#ISetup)
2. [**Data upload**](#Data-upload)
3. [**Analysis**](#Analysis)  
    a) [**Protein level**](#Protein-level)  
    b) [**Peptide level**](#Peptide-level)
4. [**Quality control of the entire sample**](#Quality-control-of-the-entire-sample)

# Setup

In [216]:
def import_diann_stats(
    filepath: str,
    experiment: str
):
    """Load the DIANN output .stats.tsv file.

    Parameters
    ----------
    filepath : str
        Full path to the .stats.tsv file.
    experiment : str
        The name of the experiment.

    Returns
    -------
    pd.DataFrame
        The output data frame contains summary information about the whole experiment.
    """
    diann_overview = pd.read_csv(filepath, sep='\t')
    diann_overview = diann_overview[diann_overview['File.Name'].str.contains(experiment)]
    diann_overview = diann_overview[diann_overview.columns[1:]].T
    diann_overview.reset_index(inplace=True)
    diann_overview.rename(columns={'index': 'parameters', 0: 'values'}, inplace=True)
    diann_overview['values'] = diann_overview['values'].apply(lambda x: '%.2E' % x if x>100000 else '%.2f' % x)
    return diann_overview


def get_protein_info(
    fasta: dict,
    protein_ids: str
):
    """Short summary.

    Parameters
    ----------
    fasta : pyteomics.fasta.IndexedUniProt object
        The Pyteomics object contains information about all proteins from the .fasta file.
    protein_ids : str
        The list of the protein IDs separated by comma.

    Returns
    -------
    type
        Description of returned object.

    """
    protein_names = []
    protein_seq_lens = []
    for protein_id in protein_ids.split():
        try:
            protein_names.append(fasta.get_by_id(protein_id).description['name'])
        except KeyError:
            logging.info(f"The protein id {protein_id} is not found in the fasta file.")
        try:
            protein_seq_lens.append(str(len(fasta.get_by_id(protein_id).sequence)))
        except KeyError:
            logging.info(f"The sequence length for the protein {protein_id} is not found in the fasta file.")
    return ','.join(protein_names), ','.join(protein_seq_lens)


def create_diann_proteins_table(
    diann_df: pd.DataFrame
):
    """Extract information about genes, proteins and protein groups from the loaded main DIANN output .tsv file.

    Parameters
    ----------
    diann_df : pd.DataFrame
        The original data frame after loading the main .tsv DIANN output file and filter by the experiment name.

    Returns
    -------
    pd.DataFrame
        The output data frame contains information about genes, proteins and proteins groups.
    """
    columns = [col for col in diann_df.columns if 'PG' in col or 'Protein' in col or 'Genes' in col]
    cols_to_remove = ['Protein.Group', 'Protein.Ids', 'Protein.Names']
    for col in cols_to_remove:
        columns.remove(col)
    proteins = diann_df.groupby(columns).agg({
        'Protein.Ids': lambda x: ','.join(set(x)),
        'MS2.Scan': lambda x: len(set(x)),
        'Stripped.Sequence': lambda x: len(set(x))
    }).reset_index()
    proteins.rename(columns={
        'MS2.Scan': '# MS/MS',
        'Stripped.Sequence': '(EXP) # peptides',
        'Genes': 'Gene names'
    }, inplace=True)
    proteins['# proteins'] = proteins['Protein.Ids'].apply(lambda x: len(x.split(',')))
    proteins['Protein names'], proteins['Sequence lengths'] = zip(
        *proteins['Protein.Ids'].apply(lambda x: get_protein_info(fasta, x)))
    first_columns = ['Protein.Ids', 'Protein names', 'Gene names', '# proteins', '(EXP) # peptides',
                     '# MS/MS', 'Sequence lengths']
    proteins = proteins[first_columns + sorted(list(set(proteins.columns).difference(first_columns)))]
    return proteins


def import_diann_output(
    path_diann_output_folder: str,
    experiment: str
):
    """Load two files from the DiaNN output folder and returns the data frames for each of the files.

    Parameters
    ----------
    path_diann_output_folder : str
        Path to the DIANN output folder with all output files needed.
    experiment : str
        The name of the experiment.

    Returns
    -------
    list of pd.DataFrames
        For each of the output files, the function returns a pandas data frame with the extracted information.
    """
    diann_output_file, diann_stats_file = sorted(alphaviz.io.get_filenames_from_directory(
        path_diann_output_folder, 'tsv'), key=len)[:2]
    
    diann_df = pd.read_csv(os.path.join(path_diann_output_folder, diann_output_file), sep='\t')
    diann_df = diann_df[diann_df.Run == experiment]
    
    diann_proteins = create_diann_proteins_table(diann_df)
    diann_peptides = create_diann_peptides_table(diann_df)
    
    diann_overview = import_diann_stats(os.path.join(path_diann_output_folder, diann_stats_file), experiment)
    
    return diann_proteins, diann_peptides, diann_overview

In [217]:
def create_diann_peptides_table(
    diann_df: pd.DataFrame
):
    """Extract information about peptides from the loaded main DIANN output .tsv file.

    Parameters
    ----------
    diann_df : pd.DataFrame
        The original data frame after loading the main .tsv DIANN output file and filter by the experiment name.

    Returns
    -------
    pd.DataFrame
        The output data frame contains information about peptides.
    """
    peptides = diann_df.copy()
    columns = [col for col in peptides.columns if not 'PG' in col and not 'Protein' in col and not 'Genes' in col and not 'GG' in col]
    columns.extend(['Genes'])
    
    peptides = diann_df[columns[2:]].copy()
    peptides['Length'] = peptides['Stripped.Sequence'].str.len()

    peptides.rename(columns={
        'MS2.Scan': 'MS/MS scan number',
        'Genes': 'Gene names',
        'Precursor.Charge': 'Charge',
        'Stripped.Sequence': 'Sequence'
    }, inplace=True)
    
    peptides['Sequence_AP_mod'] = peptides['Modified.Sequence'].apply(convert_diann_ap_mod)
    peptides['Modified.Sequence'] = peptides['Modified.Sequence'].apply(convert_diann_mq_mod)
    first_columns = ['Modified.Sequence', 'Length', 'RT', 'Predicted.RT', 'Charge', 'IM', 'Predicted.IM']
    peptides = peptides[first_columns + sorted(list(set(peptides.columns).difference(first_columns)))]
    return peptides

In [218]:
import re

def convert_diann_ap_mod(
    sequence:str
) -> str:
    # this function is copied from the AlphaMap package
    """Convert DIA-NN style modifications into MaxQuant style modifications.

    Args:
        sequence (str): The peptide sequence with modification in an AlphaPept style.

    Returns:
        str: The peptide sequence with modification in a similar to DIA-NN style.
    """

    modif_convers_dict = {
        '(UniMod:1)': 'a', #'[Acetyl ({})]'
        '(UniMod:2)': 'am', #'[Amidated ({})]'
        '(UniMod:4)': 'c', #'[Carbamidomethyl ({})]'
        '(UniMod:7)': 'deam', #'[Deamidation ({})]'
        '(UniMod:21)': 'p', #'[Phospho ({})]'
        '(UniMod:27)': 'pg', #'[Glu->pyro-Glu]'
        '(UniMod:28)': 'pg', #'[Gln->pyro-Glu]'
        '(UniMod:35)': 'ox', #'[Oxidation ({})]'
    }
    mods = re.findall('\(UniMod:\d+\)', sequence)
       
    if mods:
        for mod in mods:
            posit = re.search('\(UniMod:\d+\)', sequence)
            i = posit.start()
            if i != 0:
                i -= 1
            if mod in modif_convers_dict.keys():
                sequence = sequence.replace(mod, '', 1)
                sequence = sequence[:i] + modif_convers_dict[mod] + sequence[i:]
            else:
                logging.info(f"This modification {mod} can't be converted.")

    return sequence

def convert_diann_mq_mod(
    sequence:str
) -> str:
    """Convert DIA-NN style modifications into MaxQuant style modifications.
    Args:
        sequence (str): The peptide sequence with modification in an AlphaPept style.
    Returns:
        str: The peptide sequence with modification in a similar to DIA-NN style.
    """

    modif_convers_dict = {
        '(UniMod:1)': '[Acetyl ({})]',
        '(UniMod:2)': '[Amidated ({})]',
        '(UniMod:4)': '[Carbamidomethyl ({})]',
        '(UniMod:5)': '[Carbamyl ({})]',
        '(UniMod:7)': '[Deamidation ({})]',
        '(UniMod:21)': '[Phospho ({})]',
        '(UniMod:23)': '[Dehydrated ({})]',
        '(UniMod:26)': '[Pyro-carbamidomethyl ({})]',
        '(UniMod:27)': '[Glu->pyro-Glu]',
        '(UniMod:28)': '[Gln->pyro-Glu]',
        '(UniMod:30)': '[Cation:Na ({})]',
        '(UniMod:34)': '[Methyl ({})]',
        '(UniMod:35)': '[Oxidation ({})]',
        '(UniMod:36)': '[Dimethyl ({})]',
        '(UniMod:37)': '[Trimethyl ({})]',
        '(UniMod:40)': '[Sulfo ({})]',
        '(UniMod:55)': '[Cys-Cys]',
        '(UniMod:121)': '[GlyGly ({})]',
        '(UniMod:254)': '[Delta:H(2)C(2) ({})]',
        '(UniMod:312)': '[Cysteinyl]',
        '(UniMod:345)': '[Trioxidation ({})]',
        '(UniMod:408)': '[Hydroxyproline]',
        '(UniMod:425)': '[Dioxidation ({})]',
        '(UniMod:526)': '[Dethiomethyl ({})]',
        '(UniMod:877)': '[QQTGG ({})]',
    }
    mods = re.findall('\(UniMod:\d+\)', sequence)
    if mods:
        for mod in mods:
            posit = re.search('\(UniMod:\d+\)', sequence)
            i = posit.start()

            if i == 0:
                add_aa = 'N-term'
            elif posit.end() == len(sequence):
                add_aa = 'C-term'
            else:
                add_aa = sequence[i-1]

            if mod == '(UniMod:7)':
                if add_aa in 'NQ':
                    add_aa = 'NQ'
            elif mod == '(UniMod:21)':
                if add_aa in 'STY':
                    add_aa = 'STY'
            elif mod == '(UniMod:23)':
                if add_aa in 'ST':
                    add_aa = 'ST'
            elif mod == '(UniMod:30)':
                if add_aa in 'DE':
                    add_aa = 'DE'
            elif mod == '(UniMod:34)':
                if add_aa in 'KR':
                    add_aa = 'KR'
            elif mod == '(UniMod:36)':
                if add_aa in 'KR':
                    add_aa = 'KR'
            elif mod == '(UniMod:40)':
                if add_aa in 'STY':
                    add_aa = 'STY'
            elif mod == '(UniMod:425)':
                if add_aa in 'MW':
                    add_aa = 'MW'

            if mod in modif_convers_dict.keys():
                sequence = sequence.replace(mod, modif_convers_dict.get(mod).format(add_aa), 1)

    return sequence

In [219]:
db = mass.Unimod()
aa_comp = dict(mass.std_aa_comp)

NameError: name 'mass' is not defined

In [ ]:
# db.by_id(27), db.by_id(28)

In [ ]:
xic_tol_value = 10
xic_im_tol = 0.05
xic_tol_units = 'ppm' # options: ['ppm', 'Da']
x_axis_label = 'rt'

mz_value = 1221.990637

In [ ]:
!pip install alphapept

In [ ]:
from numba import types
from numba.typed import Dict
from numba import jit

# This code was taken from the AlphaPept Python package (https://github.com/MannLabs/alphapept/blob/master/nbs/03_fasta.ipynb)
#generates the mass dictionary from table
def get_mass_dict(modfile:str="Data/modifications.tsv", aasfile: str="Data/amino_acids.tsv", verbose:bool=True):
    """
    Function to create a mass dict based on tsv files.
    This is used to create the hardcoded dict in the constants notebook.
    The dict needs to be hardcoded because of importing restrictions when using numba.
    More specifically, a global needs to be typed at runtime.
    Args:
        modfile (str): Filename of modifications file.
        aasfile (str): Filename of AAs file.
        verbose (bool, optional): Flag to print dict.
    Returns:
        Returns a numba compatible dictionary with masses.
    Raises:
        FileNotFoundError: If files are not found.
    """
    import pandas as pd

    mods = pd.read_csv(modfile, delimiter="\t")
    aas = pd.read_csv(aasfile, delimiter="\t")

    mass_dict = Dict.empty(key_type=types.unicode_type, value_type=types.float64)

    for identifier, mass in aas[["Identifier", "Monoisotopic Mass (Da)"]].values:
        mass_dict[identifier] = float(mass)

    for identifier, aar, mass in mods[
        ["Identifier", "Amino Acid Residue", "Monoisotopic Mass Shift (Da)"]
    ].values:
        #print(identifier, aar, mass)

        if ("<" in identifier) or (">" in identifier):
            for aa_identifier, aa_mass in aas[["Identifier", "Monoisotopic Mass (Da)"]].values:
                if '^' in identifier:
                    new_identifier = identifier[:-2] + aa_identifier
                    mass_dict[new_identifier] = float(mass) + mass_dict[aa_identifier]
                elif aar == aa_identifier:
                    new_identifier = identifier[:-2] + aa_identifier
                    mass_dict[new_identifier] = float(mass) + mass_dict[aa_identifier]
                else:
                    pass
        else:
            mass_dict[identifier] = float(mass) + mass_dict[aar]

    # Manually add other masses
    mass_dict[
        "Electron"
    ] = (
        0.000548579909070
    )  # electron mass, half a millimass error if not taken into account
    mass_dict["Proton"] = 1.00727646687  # proton mass
    mass_dict["Hydrogen"] = 1.00782503223  # hydrogen mass
    mass_dict["C13"] = 13.003354835  # C13 mass
    mass_dict["Oxygen"] = 15.994914619  # oxygen mass
    mass_dict["OH"] = mass_dict["Oxygen"] + mass_dict["Hydrogen"]  # OH mass
    mass_dict["H2O"] = mass_dict["Oxygen"] + 2 * mass_dict["Hydrogen"]  # H2O mass

    mass_dict["NH3"] = 17.03052
    mass_dict["delta_M"] = 1.00286864
    mass_dict["delta_S"] = 0.0109135

    if verbose:

        for element in mass_dict:
            print('mass_dict["{}"] = {}'.format(element, mass_dict[element]))

    return mass_dict

import numba

@jit
def get_fragmass(parsed_pep:list, mass_dict:numba.typed.Dict)->tuple:
    """
    Calculate the masses of the fragment ions
    Args:
        parsed_pep (numba.typed.List of str): the list of amino acids and modified amono acids.
        mass_dict (numba.typed.Dict): key is the amino acid or the modified amino acid, and the value is the mass.
    Returns:
        Tuple[np.ndarray(np.float64), np.ndarray(np.int8)]: the fragment masses and the fragment types (represented as np.int8).
        For a fragment type, positive value means the b-ion, the value indicates the position (b1, b2, b3...); the negative value means
        the y-ion, the absolute value indicates the position (y1, y2, ...).
    """
    n_frags = (len(parsed_pep) - 1) * 2

    frag_masses = np.zeros(n_frags, dtype=np.float64)
    frag_type = np.zeros(n_frags, dtype=np.int8)

    n_frag = 0

    frag_m = mass_dict["Proton"]
    for idx, _ in enumerate(parsed_pep[:-1]):
        print(_)
        frag_m += mass_dict[_]
        frag_masses[n_frag] = frag_m
        frag_type[n_frag] = (idx+1)
        n_frag += 1

    frag_m = mass_dict["Proton"] + mass_dict["H2O"]
    for idx, _ in enumerate(parsed_pep[::-1][:-1]):
        frag_m += mass_dict[_]
        frag_masses[n_frag] = frag_m
        frag_type[n_frag] = -(idx+1)
        n_frag += 1

    return frag_masses, frag_type

In [ ]:
a = get_mass_dict()

In [ ]:
from numba import njit
from numba.typed import List
import numpy as np
import numba

@njit
def parse(peptide:str)->List:
    """
    Parser to parse peptide strings
    Args:
        peptide (str): modified peptide sequence.
    Return:
        List (numba.typed.List): a list of animo acids and modified amono acids
    """
    if "_" in peptide:
        peptide = peptide.split("_")[0]
    parsed = List()
    string = ""

    for i in peptide:
        string += i
        if i.isupper():
            parsed.append(string)
            string = ""

    return parsed

@njit
def get_precmass(parsed_pep:list, mass_dict:numba.typed.Dict)->float:
    """
    Calculate the mass of the neutral precursor
    Args:
        parsed_pep (list or numba.typed.List of str): the list of amino acids and modified amono acids.
        mass_dict (numba.typed.Dict): key is the amino acid or the modified amino acid, and the value is the mass.
    Returns:
        float: the peptide neutral mass.
    """
    tmass = mass_dict["H2O"]
    for _ in parsed_pep:
        tmass += mass_dict[_]

    return tmass

@njit
def get_fragmass(parsed_pep:list, mass_dict:numba.typed.Dict)->tuple:
    """
    Calculate the masses of the fragment ions
    Args:
        parsed_pep (numba.typed.List of str): the list of amino acids and modified amono acids.
        mass_dict (numba.typed.Dict): key is the amino acid or the modified amino acid, and the value is the mass.
    Returns:
        Tuple[np.ndarray(np.float64), np.ndarray(np.int8)]: the fragment masses and the fragment types (represented as np.int8).
        For a fragment type, positive value means the b-ion, the value indicates the position (b1, b2, b3...); the negative value means
        the y-ion, the absolute value indicates the position (y1, y2, ...).
    """
    n_frags = (len(parsed_pep) - 1) * 2

    frag_masses = np.zeros(n_frags, dtype=np.float64)
    frag_type = np.zeros(n_frags, dtype=np.int8)

    n_frag = 0

    frag_m = mass_dict["Proton"]
    for idx, _ in enumerate(parsed_pep[:-1]):
        frag_m += mass_dict[_]
        frag_masses[n_frag] = frag_m
        frag_type[n_frag] = (idx+1)
        n_frag += 1

    frag_m = mass_dict["Proton"] + mass_dict["H2O"]
    for idx, _ in enumerate(parsed_pep[::-1][:-1]):
        frag_m += mass_dict[_]
        frag_masses[n_frag] = frag_m
        frag_type[n_frag] = -(idx+1)
        n_frag += 1

    return frag_masses, frag_type

def get_frag_dict(parsed_pep:list, mass_dict:dict)->dict:
    """
    Calculate the masses of the fragment ions
    Args:
        parsed_pep (list or numba.typed.List of str): the list of amino acids and modified amono acids.
        mass_dict (numba.typed.Dict): key is the amino acid or the modified amino acid, and the value is the mass.
    Returns:
        dict{str:float}: key is the fragment type (b1, b2, ..., y1, y2, ...), value is fragment mass.
    """
    frag_dict = {}
    frag_masses, frag_type = get_fragmass(parsed_pep, mass_dict)

    for idx, _ in enumerate(frag_masses):

        cnt = frag_type[idx]
        if cnt > 0:
            identifier = 'b'
        else:
            identifier = 'y'
            cnt = -cnt
        frag_dict[identifier+str(cnt)] = _

    return frag_dict


M_PROTON = mass_dict['Proton']

@njit
def calculate_mass(mono_mz:float, charge:int) -> float:
    """Calculate the precursor mass from mono mz and charge.
    Args:
        mono_mz (float): mono m/z.
        charge (int): charge.
    Returns:
        float: precursor mass.
    """
    prec_mass = mono_mz * abs(charge) - charge * M_PROTON

    return prec_mass

@njit
def calculate_mz(prec_mass:float, charge:int) -> float:
    """Calculate the precursor mono mz from mass and charge.
    Args:
        prec_mass (float): precursor mass.
        charge (int): charge.
    Returns:
        float: mono m/z.
    """
    mono_mz = prec_mass / abs(charge) + M_PROTON

    return mono_mz

In [ ]:
import pandas as pd
import numpy as np
from numba import njit
from tqdm import tqdm
import plotly.graph_objects as go
import plotly.subplots

def plot_line(
    timstof_data,
    selected_indices: np.ndarray,
    label: str,
    remove_zeros: bool = False,
    trim: bool = True,
):
    """Plot an XIC as a lineplot.

    Parameters
    ----------
    timstof_data : alphatims.bruker.TimsTOF
        An alphatims.bruker.TimsTOF data object.
    selected_indices : np.ndarray
        The raw indices that are selected for this plot.
    label : str
        The label for the line plot.
    remove_zeros : bool
        If True, zeros are removed. Default: False.
    trim : bool
        If True, zeros on the left and right are trimmed. Default: True.

    Returns
    -------
    a Plotly line plot
        The XIC line plot.
    """
    axis_dict = {
        "rt": "RT, min",
        "intensity": "Intensity",
    }
    x_axis_label = axis_dict["rt"]
    y_axis_label = axis_dict["intensity"]
    labels = {
        'RT, min': "rt_values",
    }
    x_dimension = labels[x_axis_label]
    intensities = timstof_data.bin_intensities(selected_indices, [x_dimension])
    x_ticks = timstof_data.rt_values / 60
       
    non_zeros = np.flatnonzero(intensities)
    if len(non_zeros) == 0:
        x_ticks = np.empty(0, dtype=x_ticks.dtype)
        intensities = np.empty(0, dtype=intensities.dtype)
    else:
        if remove_zeros:
            x_ticks = x_ticks[non_zeros]
            intensities = intensities[non_zeros]
        elif trim:
            start = max(0, non_zeros[0] - 1)
            end = non_zeros[-1] + 2
            x_ticks = x_ticks[start: end]
            intensities = intensities[start: end]

    trace = go.Scatter(
        x=x_ticks,
        y=intensities,
        mode='lines',
        text = [f'{x_axis_label}'.format(i + 1) for i in range(len(x_ticks))],
        hovertemplate='<b>%{text}:</b> %{x};<br><b>Intensity:</b> %{y}.',
        name=label
    )
    return trace

def plot_elution_profile(
    bruker_raw_data,
    peptide_info: dict,
    mass_dict: dict,
    mz_tol: float = 50,
    rt_tol: float = 30,
    im_tol: float = 0.05,
    title: str = "",
    width: int = 900,
    height: int = 400
):
    """Plot an elution profile plot for the specified precursor and all his identified fragments.

    Parameters
    ----------
    bruker_raw_data : alphatims.bruker.TimsTOF
        An alphatims.bruker.TimsTOF data object.
    peptide_info : dict
        Peptide information including sequence, fragments' patterns, rt, mz and im values.
    mass_dict : dict
        The basic mass dictionaty with the masses of all amino acids and modifications.
    mz_tol: float 
        The mz tolerance value. Default: 50 ppm.
    rt_tol: float 
        The rt tolerance value. Default: 30 ppm.
    im_tol: float 
        The im tolerance value. Default: 0.05 ppm.
    title : str
        The title of the plot.
    width : int
        The width of the plot. Default: 900.
    height : int
        The height of the plot. Default: 400.

    Returns
    -------
    a Plotly line plot
        The elution profile plot in retention time dimension for the specified peptide and all his fragments.
    """
    x_axis_label = "rt"
    y_axis_label = "intensity"
    
    # predict the theoretical fragments using the Alphapept get_fragmass() function.
    frag_masses, frag_type = get_fragmass(
        parsed_pep=parse(peptide_info['sequence']), 
        mass_dict=mass_dict
    )
    peptide_info['fragments'] = {
        (f"b{key}" if key>0 else f"y{-key}"):value for key,value in zip(frag_type, frag_masses)
    }
    
    # slice the data using the rt_tol, im_tol and mz_tol values
    rt_slice = slice(peptide_info['rt'] - rt_tol, peptide_info['rt'] + rt_tol)
    im_slice = slice(peptide_info['im'] - im_tol, peptide_info['im'] + im_tol)
    prec_mz_slice = slice(peptide_info['mz'] / (1 + mz_tol / 10**6), peptide_info['mz'] * (1 + mz_tol / 10**6))
    
    # create an elution profile for the precursor
    precursor_indices = bruker_raw_data[
        rt_slice,
        im_slice,
        0,
        prec_mz_slice,
        'raw'
    ]
    fig = go.Figure()
    fig.add_trace(
        plot_line(bruker_raw_data, precursor_indices, remove_zeros=True, label='precursor')
    )
    
    # create elution profiles for all fragments
    for frag, frag_mz in peptide_info['fragments'].items():
        fragment_data_indices = bruker_raw_data[
            rt_slice,
            im_slice,
            prec_mz_slice,
            slice(frag_mz / (1 + mz_tol / 10**6), frag_mz * (1 + mz_tol / 10**6)),
            'raw'
        ]
        if len(fragment_data_indices) > 0:
            fig.add_trace(
                plot_line(bruker_raw_data, fragment_data_indices, remove_zeros=True, label=frag)
            )
    
    fig.update_layout(
        title=dict(
            text=title,
            font=dict(
                size=16,
            ),
            x=0.5,
            xanchor='center',
            yanchor='top'
        ),
        xaxis=dict(
            title=x_axis_label,
            titlefont_size=14,
            tickmode = 'auto',
            tickfont_size=14,
        ),
        yaxis=dict(
            title=y_axis_label
        ),
        legend=dict(
            orientation="h",
            yanchor="bottom",
            y=-0.6,
            xanchor="right",
            x=0.95
        ),
        template = "plotly_white", 
        width=width,
        height=height,
        hovermode="x unified",
        showlegend=True
    )
    return fig

In [ ]:
def plot_heatmap(
    df: pd.DataFrame,
    title: str = "",
    width: int = 250,
    height: int = 250,
    background_color: str = "black",
    colormap: str = "fire",
):
    """Create a heatmap showing a correlation of retention time  and ion mobility with color coding for signal intensity.

    Parameters
    ----------
    df : pandas Dataframe
        A dataframe obtained by slicing an alphatims.bruker.TimsTOF object.
    title: str
        The title of the plot. Default: "".
    width : int
        The width of the plot. Default: 250.
    height : int
        The height of the plot. Default: 250.
    background_color : str
        The background color of the plot. Default: "black".
    colormap : str
        The name of the colormap in Plotly. Default: "fire".
        
    Returns
    -------
    a Plotly scatter plot
        The scatter plot showing the correlation of retention time  and ion mobility with color coding for signal intensity.
    """
    labels = {
        'RT, min': "rt_values",
        'Inversed IM, V·s·cm\u207B\u00B2': "mobility_values",
        'Intensity': "intensity_values",
    }
    x_axis_label = "RT, min"
    y_axis_label = "Inversed IM, V·s·cm\u207B\u00B2"
    z_axis_label = "Intensity"
    
    x_dimension = labels[x_axis_label]
    y_dimension = labels[y_axis_label]
    z_dimension = labels[z_axis_label]

    df["rt_values"] /= 60

#     def hook(plot, element):
#         plot.handles['layout']['xaxis']['gridcolor'] = background_color
#         plot.handles['layout']['yaxis']['gridcolor'] = background_color
#         plot.handles['layout']['xaxis']['titlefont'] = dict(size=6)
#         plot.handles['layout']['yaxis']['titlefont'] = dict(size=6)
#         plot.handles['layout']['xaxis']['tickfont'] = dict(size=6)
#         plot.handles['layout']['yaxis']['tickfont'] = dict(size=6)

    opts_ms1=dict(
        width=width,
        height=height,
        title=title,
        xlabel=x_axis_label,
        ylabel=y_axis_label,
        bgcolor=background_color,
#         hooks=[hook],
    )
    dmap = hv.DynamicMap(
        hv.Points(
            df,
            [x_dimension, y_dimension],
            z_dimension
        )
    )
    agg = rasterize(
        dmap,
        width=width,
        height=height,
        aggregator='sum'
    )
    fig = dynspread(
        shade(
            agg,
            cmap=colormap
        )
    ).opts(plot=opts_ms1)

    return fig

def plot_elution_profile_heatmap(
    timstof_data,
    peptide_info: dict,
    mass_dict: dict,
    mz_tol: int = 50,
    rt_tol: int = 30,
    im_tol: int = 0.05,
    title: str = "",
    n_cols: int = 5,
    width: int = 180,
    height: int = 180,
):
    """Plot an elution profile for the specified precursor and all his identified fragments as heatmaps in the 
    retention time/ion mobility dimensions.

    Parameters
    ----------
    timstof_data : alphatims.bruker.TimsTOF
        An alphatims.bruker.TimsTOF data object.
    peptide_info : dict
        Peptide information including sequence, fragments' patterns, rt, mz and im values.
    mass_dict : dict
        The basic mass dictionaty with the masses of all amino acids and modifications.
    mz_tol: float 
        The mz tolerance value. Default: 50 ppm.
    rt_tol: float 
        The rt tolerance value. Default: 30 ppm.
    im_tol: float 
        The im tolerance value. Default: 0.05 ppm.
    title : str
        The title of the plot. Default: "".
    n_cols: int
        The number of the heatmaps plotted per row. Default: 5.
    width : int
        The width of the plot. Default: 180.
    height : int
        The height of the plot. Default: 180.

    Returns
    -------
    a Bokeh heatmap plots
        The elution profile heatmap plots in retention time and ion mobility dimensions 
        for the specified peptide and all his fragments.
    """
    # predict the theoretical fragments using the Alphapept get_fragmass() function.
    frag_masses, frag_type = alphaviz.utils.get_fragmass(
        parsed_pep=alphaviz.utils.parse(peptide_info['sequence']),  
        mass_dict=mass_dict
    )
    peptide_info['fragments'] = {
        (f"b{key}" if key>0 else f"y{-key}"):value for key,value in zip(frag_type, frag_masses)
    }
    
    # slice the data using the rt_tol, im_tol and mz_tol values
    rt_slice = slice(peptide_info['rt'] - rt_tol, peptide_info['rt'] + rt_tol)
    im_slice = slice(peptide_info['im'] - im_tol, peptide_info['im'] + im_tol)
    prec_mz_slice = slice(peptide_info['mz'] / (1 + mz_tol / 10**6), peptide_info['mz'] * (1 + mz_tol / 10**6))
    
    # create an elution profile for the precursor
    precursor_indices = timstof_data[
        rt_slice,
        im_slice,
        0,
        prec_mz_slice,
        'raw'
    ]
    
#     print(precursor_indices.shape)
    common_plot = plot_heatmap(
        timstof_data.as_dataframe(precursor_indices), title='precursor', width=width, height=height
    )
    
    # create elution profiles for all fragments
    for frag, frag_mz in peptide_info['fragments'].items():
        fragment_data_indices = timstof_data[
            rt_slice,
            im_slice,
            prec_mz_slice,
            slice(frag_mz / (1 + mz_tol / 10**6), frag_mz * (1 + mz_tol / 10**6)),
            'raw'
        ]
#         print(fragment_data_indices.shape)
        if len(fragment_data_indices) > 0:
            common_plot += plot_heatmap(
                timstof_data.as_dataframe(fragment_data_indices), title=frag, width=width, height=height
            )
    
    return common_plot.cols(n_cols)

### Import all necessary libraries

In [1]:
import os
import logging
import pandas as pd
from io import StringIO

import alphatims.bruker
import alphatims.utils

# visualization
import panel as pn
import bokeh.server.views.ws
from bokeh.models.widgets.tables import NumberFormatter
import holoviews as hv
from bokeh.io import export_svgs

from holoviews import opts
from holoviews.operation.datashader import dynspread, rasterize, shade, datashade

# local
import alphaviz
import alphaviz.utils
import alphaviz.io
import alphaviz.preprocessing
import alphaviz.plotting

### Set paths to raw data, software analysis (MaxQuant, DiaNN) output folder, fasta file

In [3]:
# path to the .d folder or .hdf file
# experimental_file = '/Users/eugeniavoytik/copied/Bruker/MaxQuant_output_tables/20210413_TIMS03_EVO03_PaSk_MA_HeLa_200ng_S1-A1_1_24848.hdf'
# path to the .txt MQ output folder
# mq_output_folder = '/Users/eugeniavoytik/copied/Bruker/MaxQuant_output_tables/20210413_TIMS03_EVO03_PaSk_MA_HeLa_200ng_S1-A1_1_24848.d/txt'
experimental_file = '/Users/eugeniavoytik/Projects/DIANN/high_speed_already_published_method/20201218_tims03_Evo03_PS_SA_HeLa_200ng_high_speed_21min_8cm_S2-B8_1_22654.d'
diann_output_folder = '/Users/eugeniavoytik/Projects/DIANN/high_speed_already_published_method'
# diann_output_folder = '/Users/eugeniavoytik/Projects/DIANN/LiDIAnewMSmethod'
# experimental_file = 
# path to the fasta file
fasta_file = '/Users/eugeniavoytik/copied/Bruker/MaxQuant_output_tables/20210413_TIMS03_EVO03_PaSk_MA_HeLa_200ng_S1-A1_1_24848.d/txt/human.fasta'


In [80]:
# not identified by DIANN
experimental_file = '/Users/eugeniavoytik/Projects/DIANN_peptides_per_protein/4.Targeted_analysis_positional_phosphoisomers/dia-PASEF_in_theory_contain_all_peptides_with_diff_total_intensity/20210407_tims03_Evo03_PaSk_SA_pos_isomers_all_2500fmol_S4-A5_1_24586.d'

# Data upload

### 1) Load the raw file

In [81]:
# Bruker
raw_data = alphatims.bruker.TimsTOF(experimental_file)

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 12010/12010 [00:03<00:00, 3609.73it/s]


### 2) Load the fasta file

In [116]:
fasta = alphaviz.io.read_fasta(fasta_file)

### 3) Load the output folder of any supported software processing tool (currently MaxQuant)

In [117]:
proteins, peptides, statist = alphaviz.io.import_diann_output(
    diann_output_folder, 
    '20201218_tims03_Evo03_PS_SA_HeLa_200ng_high_speed_21min_8cm_S2-B8_1_22654',
    fasta
)

In [118]:
proteins.head()

Protein IDs                                 Protein names Gene names  \
0      P01023                         Alpha-2-macroglobulin        A2M   
1      Q9NRG9                                        Aladin       AAAS   
2      Q86V21                    Acetoacetyl-CoA synthetase       AACS   
3      Q6PD74  Alpha- and gamma-adaptin-binding protein p34      AAGAB   
4    Q2M2I8-2  Isoform 2 of AP2-associated protein kinase 1       AAK1   

   # proteins  (EXP) # peptides  # MS/MS Sequence lengths  Genes.MaxLFQ  \
0           1                 2        2             1474      32609.70   
1           1                14       17              546      71502.60   
2           1                14       14              672      25143.70   
3           1                 2        3              315      28522.00   
4           1                 4        4              863       4518.81   

   Genes.MaxLFQ.Unique  Genes.Normalised  Genes.Quantity  Global.PG.Q.Value  \
0             32609.70          31608.50        31859.30           0.000146   
1             71502.60          71717.60        72286.60           0.000146   
2             25143.70          23294.30        23479.20           0.000146   
3             28522.00          28657.80        28885.10           0.000146   
4              4518.81           4454.43         4489.78           0.000146   

   PG.MaxLFQ  PG.Normalised  PG.Q.Value  PG.Quantity  Protein.Q.Value  
0   32609.70       31608.50    0.000154     31859.30         0.000154  
1   71502.60       71717.60    0.000154     72286.60         0.000154  
2   25143.70       23294.30    0.000154     23479.20         0.000154  
3   28522.00       28657.80    0.000154     28885.10         0.000154  
4    4518.81        4454.43    0.000154      4489.78         0.000154

In [36]:
alphaviz.plotting.plot_pept_per_protein_barplot(proteins, '(EXP) # peptides', 'Peptides per protein')

## Discovery mode

In [82]:
mass_dict = alphaviz.utils.get_mass_dict(verbose=False)

In [102]:
# a peptide not identified by any software tool
rab10_unmod = {
    "sequence": 'FHTITTSYYR',
    "charge": 2,
    "im": 0.9360957,
    "rt": 7.66 * 60,
}
rab10_T72 = {
    "sequence": 'FHpTITTSYYR',
    "charge": 2,
    "im": 0.94,
    "rt": 8.3 * 60,
}
rab10_T74 = {
    "sequence": 'FHTIpTTSYYR',
    "charge": 2,
    "im": 0.97,
    "rt": 8.4 * 60,
}
rab10_T75 = {
    "sequence": 'FHTITpTSYYR',
    "charge": 2,
    "im": 0.96,
    "rt": 8.8 * 60,
}
rab10_S76 = {
    "sequence": 'FHTITTpSYYR',
    "charge": 2,
    "im": 0.96,
    "rt": 7.2 * 60,
}
rab10_Y77 = {
    "sequence": 'FHTITTSpYYR',
    "charge": 2,
    "im": 0.95,
    "rt": 7.1 * 60,
}
rab10_Y78 = {
    "sequence": 'FHTITTSYpYR',
    "charge": 2,
    "im": 0.96,
    "rt": 7.66 * 60,
}

In [112]:
for peptide in [
    rab10_unmod, 
    rab10_T72, 
    rab10_T74, 
    rab10_T75,
    rab10_S76,
    rab10_Y77,
    rab10_Y78
]:
    peptide['mz'] = alphaviz.utils.calculate_mz(
        prec_mass=alphaviz.utils.get_precmass(
            alphaviz.utils.parse(peptide['sequence']), 
            mass_dict
        ), 
        charge=peptide['charge']
    )
    print(peptide)
    print(f"rt {peptide['rt'] / 60}")
    alphaviz.plotting.plot_elution_profile(
        raw_data, 
        peptide,
        mass_dict,
        mz_tol=50,
        rt_tol=50,
        im_tol=0.03,
    ).show()

{'sequence': 'FHTITTSYYR', 'charge': 2, 'im': 0.9360957, 'rt': 459.6, 'mz': 644.8196697735999, 'fragments': {'b1': 148.07569036687, 'b2': 285.13460226687, 'b3': 386.18228076687, 'b4': 499.26634476687, 'b5': 600.31402326687, 'b6': 701.3617017668699, 'b7': 788.3937301968699, 'b8': 951.4570587968699, 'b9': 1114.5203873968699, 'y1': 175.11895215033002, 'y2': 338.18228075033005, 'y3': 501.24560935033, 'y4': 588.27763778033, 'y5': 689.32531628033, 'y6': 790.3729947803299, 'y7': 903.4570587803299, 'y8': 1004.5047372803299, 'y9': 1141.5636491803298}}
rt 7.66


{'sequence': 'FHpTITTSYYR', 'charge': 2, 'im': 0.94, 'rt': 498.00000000000006, 'mz': 684.8028352335999, 'fragments': {'b1': 148.07569036687, 'b2': 285.13460226687, 'b3': 466.14861168687, 'b4': 579.23267568687, 'b5': 680.28035418687, 'b6': 781.32803268687, 'b7': 868.3600611168699, 'b8': 1031.42338971687, 'b9': 1194.4867183168699, 'y1': 175.11895215033002, 'y2': 338.18228075033005, 'y3': 501.24560935033, 'y4': 588.27763778033, 'y5': 689.32531628033, 'y6': 790.3729947803299, 'y7': 903.4570587803299, 'y8': 1084.47106820033, 'y9': 1221.5299801003298}}
rt 8.3


{'sequence': 'FHTIpTTSYYR', 'charge': 2, 'im': 0.97, 'rt': 504.0, 'mz': 684.8028352335999, 'fragments': {'b1': 148.07569036687, 'b2': 285.13460226687, 'b3': 386.18228076687, 'b4': 499.26634476687, 'b5': 680.28035418687, 'b6': 781.32803268687, 'b7': 868.3600611168699, 'b8': 1031.42338971687, 'b9': 1194.4867183168699, 'y1': 175.11895215033002, 'y2': 338.18228075033005, 'y3': 501.24560935033, 'y4': 588.27763778033, 'y5': 689.32531628033, 'y6': 870.3393257003299, 'y7': 983.42338970033, 'y8': 1084.47106820033, 'y9': 1221.5299801003298}}
rt 8.4


{'sequence': 'FHTITpTSYYR', 'charge': 2, 'im': 0.96, 'rt': 528.0, 'mz': 684.8028352335999, 'fragments': {'b1': 148.07569036687, 'b2': 285.13460226687, 'b3': 386.18228076687, 'b4': 499.26634476687, 'b5': 600.31402326687, 'b6': 781.32803268687, 'b7': 868.3600611168699, 'b8': 1031.42338971687, 'b9': 1194.4867183168699, 'y1': 175.11895215033002, 'y2': 338.18228075033005, 'y3': 501.24560935033, 'y4': 588.27763778033, 'y5': 769.29164720033, 'y6': 870.3393257003299, 'y7': 983.42338970033, 'y8': 1084.47106820033, 'y9': 1221.5299801003298}}
rt 8.8


{'sequence': 'FHTITTpSYYR', 'charge': 2, 'im': 0.96, 'rt': 432.0, 'mz': 684.8028352335999, 'fragments': {'b1': 148.07569036687, 'b2': 285.13460226687, 'b3': 386.18228076687, 'b4': 499.26634476687, 'b5': 600.31402326687, 'b6': 701.3617017668699, 'b7': 868.3600611168699, 'b8': 1031.42338971687, 'b9': 1194.4867183168699, 'y1': 175.11895215033002, 'y2': 338.18228075033005, 'y3': 501.24560935033, 'y4': 668.24396870033, 'y5': 769.29164720033, 'y6': 870.3393257003299, 'y7': 983.42338970033, 'y8': 1084.47106820033, 'y9': 1221.5299801003298}}
rt 7.2


{'sequence': 'FHTITTSpYYR', 'charge': 2, 'im': 0.95, 'rt': 426.0, 'mz': 684.8028352335999, 'fragments': {'b1': 148.07569036687, 'b2': 285.13460226687, 'b3': 386.18228076687, 'b4': 499.26634476687, 'b5': 600.31402326687, 'b6': 701.3617017668699, 'b7': 788.3937301968699, 'b8': 1031.42338971687, 'b9': 1194.4867183168699, 'y1': 175.11895215033002, 'y2': 338.18228075033005, 'y3': 581.21194027033, 'y4': 668.24396870033, 'y5': 769.29164720033, 'y6': 870.3393257003299, 'y7': 983.42338970033, 'y8': 1084.47106820033, 'y9': 1221.5299801003298}}
rt 7.1


{'sequence': 'FHTITTSYpYR', 'charge': 2, 'im': 0.96, 'rt': 459.6, 'mz': 684.8028352335999, 'fragments': {'b1': 148.07569036687, 'b2': 285.13460226687, 'b3': 386.18228076687, 'b4': 499.26634476687, 'b5': 600.31402326687, 'b6': 701.3617017668699, 'b7': 788.3937301968699, 'b8': 951.4570587968699, 'b9': 1194.4867183168699, 'y1': 175.11895215033002, 'y2': 418.14861167033, 'y3': 581.21194027033, 'y4': 668.24396870033, 'y5': 769.29164720033, 'y6': 870.3393257003299, 'y7': 983.42338970033, 'y8': 1084.47106820033, 'y9': 1221.5299801003298}}
rt 7.66


In [113]:
mass_dict

DictType[unicode_type,float64]<iv=None>({A: 71.0371138, C: 103.0091845, D: 115.0269431, E: 129.0425931, F: 147.0684139, G: 57.02146373, H: 137.0589119, I: 113.084064, K: 128.094963, L: 113.084064, M: 131.0404846, N: 114.0429275, P: 97.05276386, Q: 128.0585775, R: 156.101111, S: 87.03202843, T: 101.0476785, U: 150.9536333957, V: 99.06841392, W: 186.079313, Y: 163.0633286, cC: 160.03064823, oxM: 147.03539923000002, aA: 113.04767849000001, aC: 145.01974919, aD: 157.03750779, aE: 171.05315779, aF: 189.07897859, aG: 99.03202842, aH: 179.06947659, aI: 155.09462869, aK: 170.10552769, aL: 155.09462869, aM: 173.05104929, aN: 156.05349219000001, aP: 139.06332855, aQ: 170.06914219, aR: 198.11167569, aS: 129.04259312, aT: 143.05824319, aU: 192.9641980857, aV: 141.07897861, aW: 228.08987769, aY: 205.07389329, amA: 70.053098207, amC: 102.02516890700001, amD: 114.042927507, amE: 128.058577507, amF: 146.084398307, amG: 56.037448137, amH: 136.074896307, amI: 112.100048407, amK: 127.11094740700001, amL:

In [99]:
alphaviz.plotting.plot_elution_profile(
    raw_data, 
    peptide,
    mass_dict,
    mz_tol=50,
    rt_tol=30,
    im_tol=0.05,
#     title=f"Precursor/fragments elution profile of {peptides_table.loc[selected_peptide_index, 'Modified.Sequence']} in RT dimension ({peptide['rt'] / 60: .2f} min)"
)#.show(config=utils.config)

In [88]:
pn.extension('bokeh')
pn.pane.HoloViews(
    alphaviz.plotting.plot_elution_profile_heatmap(
        raw_data,
        peptide,
        mass_dict,
        mz_tol=50,
        rt_tol=30,
        im_tol=0.05,
        n_cols=5,
        width=180,
        height=180
        # title=f"Precursor/fragments elution profile of {self.peptides_table.selected_dataframe['Modified.Sequence'].values[0]} in RT dimension ({self.peptide['rt'] / 60: .2f} min)"
    )
)

HoloViews(Layout)

# Analysis

To start the analysis, show the "Chromatograms" plot that visualises the total ion chromatograms and the base peak chromatograms for MS1 and MS2 data.

In [37]:
chromatograms_plot = alphaviz.plotting.plot_chrom(raw_data)
chromatograms_plot

## Protein level

To assess the quality of each protein individually, provide the gene name of the protein.

In [38]:
gene_name = 'OLFM1'

In [39]:
# get the sequence of the specified protein from the fasta file
protein_seq = alphaviz.preprocessing.get_aa_seq(
    proteins[proteins['Gene names'] == gene_name]['Protein IDs'].values[0],
    fasta,
)
protein_seq

'MSVPLLKIGVVLSTMAMITNWMSQTLPSLVGLNTTKLSAAGGGTLDRSTGVLPTNPEESWQVYSSAQDSEGRCICTVVAPQQTMCSRDARTKQLRQLLEKVQNMSQSIEVLDRRTQRDLQYVEKMENQMKGLESKFKQVEESHKQHLARQFKAIKAKMDELRPLIPVLEEYKADAKLVLQFKEEVQNLTSVLNELQEEIGAYDYDELQSRVSNLEERLRACMQKLACGKLTGISDPVTVKTSGSRFGSWMTDPLAPEGDNRVWYMDGYHNNRFVREYKSMVDFMNTDNFTSHRLPHPWSGTGQVVYNGSIYFNKFQSHIIIRFDLKTETILKTRSLDYAGYNNMYHYAWGGHSDIDLMVDESGLWAVYATNQNAGNIVVSRLDPVSLQTLQTWNTSYPKRSAGEAFIICGTLYVTNGYSGGTKVHYAYQTNASTYEYIDIPFQNKYSHISMLDYNPKDRALYAWNNGHQILYNVTLFHVIRSDEL'

Here you can see a filtered data frame containing information on **all peptides** identified for the selected protein.

In [40]:
peptides_table = peptides[peptides['Gene names'] == gene_name]
peptides_table.sort_values('Quantity.Quality', ascending=False)

Modified.Sequence  Length       RT  Predicted.RT  Charge       IM  \
183910   MDELRPLIPVLEEYK      15  16.2768       16.2426       3  0.84625   

        Predicted.IM    CScore  Decoy.CScore  Decoy.Evidence  ...   Q.Value  \
183910      0.839879  0.999983      0.000022        0.088891  ...  0.000044   

       Quantity.Quality RT.Start  RT.Stop         Sequence  Sequence_AP_mod  \
183910          0.83459  16.2291  16.3245  MDELRPLIPVLEEYK  MDELRPLIPVLEEYK   

        Spectrum.Similarity  Translated.Q.Value       iIM      iRT  
183910             0.467771                   0  0.844332  91.6458  

[1 rows x 38 columns]

To explore the position of identified peptides on a protein sequence, plot protein coverage for all peptides simultaneously or just for selected peptide (see below).

In [41]:
protein_coverage_plot = alphaviz.plotting.plot_sequence_coverage(
    protein_seq,
    gene_name,
    peptides_table['Sequence'].tolist()
)
protein_coverage_plot

## Peptide level

From this point onwards, we are going to assess the individual quality of each peptide.

In [42]:
# specify the index of the peptide that you'd like to explore further
selected_peptide_index = 183910

In [43]:
protein_coverage_plot_one_peptide = alphaviz.plotting.plot_sequence_coverage(
    protein_seq,
    gene_name,
    [peptides_table.loc[selected_peptide_index, 'Sequence']]
)
protein_coverage_plot_one_peptide

In [44]:
scan_number = [int(scan) for scan in [peptides_table.loc[selected_peptide_index, 'MS/MS scan number']]]
ms2_frame = raw_data.fragment_frames[raw_data.fragment_frames.index.isin(scan_number)].Frame.values[0]
raw_data.fragment_frames[raw_data.fragment_frames.index.isin(scan_number)]

Frame  Precursor  ScanNumBegin  ScanNumEnd  IsolationMz  \
24553   9209          1           566         725        612.5   

       IsolationWidth  CollisionEnergy  
24553            25.0        32.242152

In [45]:
ms1_frame = raw_data.frames[(raw_data.frames.MsMsType == 0) & (raw_data.frames.Id < ms2_frame)].iloc[-1, 0]
# information about the MS1 frames as keys and (MS2 frames and precursor ID) as values
ms1_ms2_frames = {ms1_frame: ms2_frame}
ms1_ms2_frames

{9208: 9209}

Specify the parameters for building the XIC/mobilogram.

In [129]:
peptides['Gene names'].sort_values()

168450     A2M
206612     A2M
6078      AAAS
86669     AAAS
111408    AAAS
          ... 
237167     NaN
237178     NaN
253705     NaN
255481     NaN
261177     NaN
Name: Gene names, Length: 74033, dtype: object

In [133]:
proteins_table = pn.widgets.Tabulator(
    proteins,
    layout='fit_data_table',
    name='Proteins table',
    pagination='remote',
    page_size=5,
    disabled=True,
    height=250,
    show_index=False,
    selectable=1,
    formatters={
        "Protein IDs": {
            'type': 'link',
            'urlPrefix':"https://www.uniprot.org/uniprot/",
            'target':"_blank",
        }
    },
    # formatters={
    #     '(EXP) Seq coverage, %': {
    #         'type': 'progress',
    #         'max': 100,
    #         'legend': True
    #     },
    #     'Protein names': {
    #         'type': "textarea"
    #     },
    # },
    # widths={
    #     'Protein IDs': 230,
    #     'Protein names': 350,
    #     'Sequence lengths': 150,
    # },
    sizing_mode='stretch_width',
    align='center',
    text_align='center',
    margin=(0, 5, 10, 5)
)

peptides_table = pn.widgets.Tabulator(
    peptides[peptides['Gene names'] == 'AAAS'],
    layout='fit_data_table',
    pagination='remote',
    page_size=8,
    disabled=True,
    height=300,
    show_index=False,
    selectable=1,
    sizing_mode='stretch_width',
    align='center',
    text_align='center',
    margin=(0, 5, 10, 5)
)

pn.extension('tabulator')
pn.Column(
    proteins_table, 
    peptides_table
)

Column
    [0] Tabulator(align='center', disabled=True, formatters={'Protein IDs': {'type': '...}, height=250, margin=(0, 5, 10, 5), name='Proteins table', page_size=5, pagination='remote', show_index=False, sizing_mode='stretch_width', text_align='center', value=     Protein I...)
    [1] Tabulator(align='center', disabled=True, height=300, margin=(0, 5, 10, 5), page_size=8, pagination='remote', show_index=False, sizing_mode='stretch_width', text_align='center', value=              ...)

In [94]:
proteins[(proteins['(EXP) # peptides'] == 1) & (proteins['# MS/MS'] > 1)]

Protein IDs                                      Protein names  \
92        P68032                      Actin, alpha cardiac muscle 1   
93        P63261                               Actin, cytoplasmic 2   
167       Q6RW13  Type-1 angiotensin II receptor-associated protein   
177       P02765                            Alpha-2-HS-glycoprotein   
183     Q13155-2  Isoform 2 of Aminoacyl tRNA synthase complex-i...   
348       P02656                               Apolipoprotein C-III   
365     O15033-2  Isoform 2 of Apoptosis-resistant E3 ubiquitin ...   
415       Q8N8R7                             ARL14 effector protein   
425       Q96BM9            ADP-ribosylation factor-like protein 8A   
432       Q9H6L4              Armadillo repeat-containing protein 7   
487     P18846-2  Isoform 2 of Cyclic AMP-dependent transcriptio...   
510       P54259                                         Atrophin-1   
540       P27449    V-type proton ATPase 16 kDa proteolipid subunit   
1204      Q9P003                        Protein cornichon homolog 4   
1426      O14569        Cytochrome b561 domain-containing protein 2   
1773      Q05639                        Elongation factor 1-alpha 2   
1841      Q13541  Eukaryotic translation initiation factor 4E-bi...   
1867      P60002          Transcription elongation factor 1 homolog   
2512      P16403                                       Histone H1.2   
2618      P01893  Putative HLA class I histocompatibility antige...   
2655    P61978-3  Isoform 3 of Heterogeneous nuclear ribonucleop...   
2744      Q9Y5U9   Immediate early response 3-interacting protein 1   
2794    Q9UK53-2         Isoform 2 of Inhibitor of growth protein 1   
2932    P24390-2  Isoform 2 of ER lumen protein-retaining recept...   
3132    P02545-2                          Isoform C of Prelamin-A/C   
3169      Q9Y546          Leucine-rich repeat-containing protein 42   
3199    P36941-2  Isoform 2 of Tumor necrosis factor receptor su...   
3259      A6NCE7  Microtubule-associated proteins 1A/1B light ch...   
3565      O75394           39S ribosomal protein L33, mitochondrial   
3588      Q9BQC6                Ribosomal protein 63, mitochondrial   
3646      P03897             NADH-ubiquinone oxidoreductase chain 3   
3846      O95139  NADH dehydrogenase [ubiquinone] 1 beta subcomp...   
3946    P15531-2       Isoform 2 of Nucleoside diphosphate kinase A   
4048      P30990                           Neurotensin/neuromedin N   
4255    Q15366-5            Isoform 5 of Poly(rC)-binding protein 2   
4264      Q86SE9               Polycomb group RING finger protein 5   
4676      P62714  Serine/threonine-protein phosphatase 2A cataly...   
5081    Q5RL73-2                Isoform 2 of RNA-binding protein 48   
5229    Q9UBF6-4                    Isoform 4 of RING-box protein 2   
5428    Q9H0E3-3  Isoform 3 of Histone deacetylase complex subun...   
5802      Q96KF7                  Small integral membrane protein 8   
5917      Q8TCT8                   Signal peptide peptidase-like 2A   
5978    Q9UNL2-2  Isoform 2 of Translocon-associated protein sub...   
6124      Q12962   Transcription initiation factor TFIID subunit 10   
6414      P62328                                    Thymosin beta-4   
6479    O43399-2                     Isoform 2 of Tumor protein D54   
6530      O43715            TP53-regulated inhibitor of apoptosis 1   
6649      Q9BQE3                             Tubulin alpha-1C chain   
6818      Q9UDW1                  Cytochrome b-c1 complex subunit 9   
6959      Q9NQA3                       WAS protein family homolog 6   
7083      P62699                              Protein yippee-like 5   
7211    Q8NEK5-2               Isoform 2 of Zinc finger protein 548   

     Gene names  # proteins  (EXP) # peptides  # MS/MS Sequence lengths  \
92        ACTC1           1                 1        4              377   
93        ACTG1           1                 1        3              375   
167      AGTRAP 

In [57]:
peptide = {
    "sequence": peptides_table.loc[selected_peptide_index, 'Sequence_AP_mod'],
    "charge": peptides_table.loc[selected_peptide_index, 'Charge'],
    "im": peptides_table.loc[selected_peptide_index, 'IM'],
    "rt": peptides_table.loc[selected_peptide_index, 'RT'] * 60      
}

print(f"The quality score of the peptide: {peptides_table.loc[selected_peptide_index, 'Quantity.Quality']}.")
peptide['mz'] = alphaviz.utils.calculate_mz(
    prec_mass=alphaviz.utils.get_precmass(
        alphaviz.utils.parse(peptide['sequence']), 
        mass_dict
    ), 
    charge=peptide['charge']
)
alphaviz.plotting.plot_elution_profile(
    raw_data, 
    peptide,
    mass_dict,
    mz_tol=50,
    rt_tol=30,
    im_tol=0.05,
    title=f"Precursor/fragments elution profile of {peptides_table.loc[selected_peptide_index, 'Modified.Sequence']} in RT dimension ({peptide['rt'] / 60: .2f} min)"
)#.show(config=utils.config)

The quality score of the peptide: 0.83459.


Slice the raw data based on the precursor mz, m/z and im tolerance.

In [ ]:
timstof_data=raw_data 
peptide_info=peptide
mass_dict=mass_dict
mz_tol= 50
rt_tol= 30
im_tol= 0.05
title= ""
n_cols= 5
width= 180
height = 180

frag_masses, frag_type = alphaviz.utils.get_fragmass(
    parsed_pep=alphaviz.utils.parse(peptide_info['sequence']),  
    mass_dict=mass_dict
)
peptide_info['fragments'] = {
    (f"b{key}" if key>0 else f"y{-key}"):value for key,value in zip(frag_type, frag_masses)
}

# slice the data using the rt_tol, im_tol and mz_tol values
rt_slice = slice(peptide_info['rt'] - rt_tol, peptide_info['rt'] + rt_tol)
im_slice = slice(peptide_info['im'] - im_tol, peptide_info['im'] + im_tol)
prec_mz_slice = slice(peptide_info['mz'] / (1 + mz_tol / 10**6), peptide_info['mz'] * (1 + mz_tol / 10**6))

# create an elution profile for the precursor
precursor_indices = timstof_data[
    rt_slice,
    im_slice,
    0,
    prec_mz_slice,
    'raw'
]

#     print(precursor_indices.shape)
# common_plot = plot_heatmap(
#     timstof_data.as_dataframe(precursor_indices), title='precursor', width=width, height=height
# )

In [ ]:
timstof_data.as_dataframe(precursor_indices)

In [ ]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x = timstof_data.as_dataframe(precursor_indices).rt_values_min,
        y = timstof_data.as_dataframe(precursor_indices).mobility_values,
        xaxis = 'x',
        yaxis = 'y',
        mode = 'markers',
        marker = dict(
            color = 'rgba(0,0,0,0.3)',
            size = 3,
            opacity = 0.2,
            colorscale='fire'
        ),
        name=" ",
    )
)
fig.update_layout(template = "plotly_dark")

In [ ]:
import holoviews.operation.datashader as hd
from datashader.colors import Hot
shaded = hd.datashade(hv.Points(timstof_data.as_dataframe(precursor_indices), ['rt_values_min', 'mobility_values']), 
                      cmap=Hot, aggregator=ds.sum('intensity_values'))
z = hd.dynspread(shaded, threshold=0.5, max_px=4)
z.opts(bgcolor='black', xaxis=None, yaxis=None, width=900, height=500)

In [ ]:
import holoviews as hv
from bokeh.io import export_svg

def export_to_svg(obj, filename):
    plot_state = hv.renderer('bokeh').get_plot(obj).state
    plot_state.output_backend = 'svg'
    export_svg(plot_state, filename=filename)

# overlay = hv.Overlay(...)
export_to_svg(z, 'overlay.svg',)

In [ ]:
proteins[proteins['(EXP) # peptides'] < 3].shape[0]

In [ ]:
statist

In [ ]:
import plotly.express as px
import pandas as pd
import numpy as np
import datashader as ds
from datashader import transfer_functions as tf

cvs = ds.Canvas(plot_width=400, plot_height=400)
agg = cvs.points(timstof_data.as_dataframe(precursor_indices), 'rt_values_min', 'mobility_values',
                ds.sum('intensity_values'))
# zero_mask = agg.values == 0
# agg.values = np.log10(agg.values, where=np.logical_not(zero_mask))
# agg.values[zero_mask] = np.nan
# fig = px.imshow(agg, origin='lower', labels={'color':'Log10(count)'})
# fig.update_traces(hoverongaps=False)
# # fig.update_layout(coloraxis_colorbar=dict(title='Count', tickprefix='1.e'))
# img = tf.shade(agg)
fig = px.imshow(agg, color_continuous_scale='RdBu_r')
fig.update_layout(template = "plotly_dark")
fig.show()

In [ ]:
agg.values

In [ ]:
pn.Column(
# export_svg(
    plot_elution_profile_heatmap(
        raw_data, 
        peptide,
        mass_dict,
        n_cols=5,
#         height=200,
#         width=200
    #     shared_axes=False
    #     x_axis_label = "RT, min",
    #     y_axis_label = "Inversed IM, V·s·cm\u207B\u00B2"
    ),
#     'test.svg'
#     alphaviz.plotting.plot_heatmap(
#     raw_data[ms1_frame],
#     mz=peptide['mz'],
#     im=peptide['im'],
#     x_axis_label='m/z, Th',
#     y_axis_label='Inversed IM, V·s·cm\u207B\u00B2',
#     title=f'MS1 frame(s) #{ms1_frame}',
#     colormap='fire',
#     background_color='black',
#     precursor_size=15,
#     precursor_color='blue',
#     framewise=True
#     )
)

In [ ]:
Visualize the MS1 or MS2 frame for the selected peptide with the location where the precursor has been selected for analysis.

In [ ]:
ms1 = alphaviz.plotting.plot_heatmap(
    raw_data[ms1_frame],
    mz=peptide['mz'],
    im=peptide['im'],
    x_axis_label='m/z, Th',
    y_axis_label='Inversed IM, V·s·cm\u207B\u00B2',
    title=f'MS1 frame(s) #{ms1_frame}',
    colormap='fire',
    background_color='black',
    precursor_size=15,
    precursor_color='blue',
)

In [ ]:
a = alphaviz.plotting.plot_heatmap(
    raw_data[ms2_frame],
    mz=peptide['mz'],
    im=peptide['im'],
    x_axis_label='m/z, Th',
    y_axis_label='Inversed IM, V·s·cm\u207B\u00B2',
    title=f'MS2 frame(s) #{ms2_frame}',
    colormap='fire',
    background_color='black',
    precursor_size=15,
    precursor_color='blue',
)

In [ ]:
import holoviews as hv
from bokeh.io import export_svg

def export_svg(obj, filename):
    plot_state = hv.renderer('bokeh').get_plot(obj).state
    plot_state.output_backend = 'svg'
    export_svg(plot_state, filename=filename)

# overlay = hv.Overlay(...)
export_svg(ms1, 'overlay.svg',)

In [ ]:
dictionary = {
    'maxquant': {
        'peptides_table': {
#             'value': self.data.evidence.loc[:, :'Andromeda score'],
            'formatters': {
                'Acetylation (N-term)': {
                    'type': 'tickCross',
                    'allowTruthy': True
                },
                'Oxidation (M)': {
                    'type': 'tickCross',
                    'allowTruthy': True
                },
#                 'Mass': NumberFormatter(format='0,0.000'),
#                 'm/z': NumberFormatter(format='0,0.000'),
#                 '1/K0': NumberFormatter(format='0,0.000'),
#                 'Intensity': NumberFormatter(format='0,0'),
#                 'MS/MS scan number': NumberFormatter(format='0,0'),
#                 'Andromeda score':  NumberFormatter(format='0,0.0'),
            },
            'widths': {
                'Sequence': 220,
                'Proteins': 200,
                'MS/MS scan number': 100,
                'Oxidation (M)': 130,
            },
        }, 
        'proteins_table': {
            'value': 'self.data.protein_groups',
            'formatters': {
                '(EXP) Seq coverage, %': {
                    'type': 'progress',
                    'max': 100,
                    'legend': True
                },
                'Protein names': {
                    'type': "textarea"
                },
            },
            'widths': {
                'Protein IDs': 230,
                'Protein names': 350,
                'Sequence lengths': 150,
            },
        }
    },
    'diann': {
        'peptides_table': {}, 
        'proteins_table': {}
    }
}

import json

with open('parameters.json', 'w') as fp:
    json.dump(dictionary, fp)

In [ ]:
# !pip install selenium
!conda install -c conda-forge firefox geckodriver -y

In [ ]:
def export_svg(obj, filename):
    plot_state = hv.renderer('bokeh').get_plot(obj).state
    plot_state.output_backend = 'svg'
    export_svgs(plot_state, filename=filename)

export_svg(a, 'overlay.svg')

In [ ]:
prec_mono_mz = peptide['mz']
if xic_tol_units == 'ppm':
    prec_mono_low_mz = prec_mono_mz / (1 + xic_tol_value / 10**6)
    prec_mono_high_mz = prec_mono_mz * (1 + xic_tol_value / 10**6)
else:
    prec_mono_low_mz = prec_mono_mz - xic_tol_value
    prec_mono_high_mz = prec_mono_mz + xic_tol_value
if x_axis_label == 'rt':
    one_over_k0 = peptide['im']
    one_over_k0_low, one_over_k0_high = one_over_k0 - xic_im_tol, one_over_k0 + xic_im_tol
    precursor_indices = raw_data[
        :,
        one_over_k0_low : one_over_k0_high,
        :,
        prec_mono_low_mz : prec_mono_high_mz,
        'raw'
    ]
else:
    precursor_indices = raw_data[
        :,
        :,
        :,
        prec_mono_low_mz : prec_mono_high_mz,
        'raw'
    ]

Visualize the extracted ion chromatogram or mobilogram for the selected peptide.

In [ ]:
alphaviz.plotting.plot_line(
    raw_data,
    precursor_indices,
    'mobility' # options: ['rt', 'mobility']
)

Visualize the MS2 spectrum with a mass error plot for each ion and annotated peptide sequence as subplots.

In [ ]:
data_ions = alphaviz.preprocessing.get_mq_ms2_scan_data(
    msms,
    scan_number[0],
    raw_data,
    ms1_ms2_frames[current_frame][1]
)

ms_spectra_plot = alphaviz.plotting.plot_mass_spectra(
    data_ions,
    title=f'MS2 spectrum for Precursor: {ms1_ms2_frames[current_frame][1]}',
    sequence=peptides_table.loc[selected_peptide_index, 'Sequence']
)
ms_spectra_plot

# Quality control of the entire sample

Here you can find several quality control plots for the entire sample. 

In [ ]:
uncalb_mass_dens_plot = alphaviz.plotting.plot_mass_error(
    evidence,
    'm/z',
    'Uncalibrated mass error [ppm]',
    'Uncalibrated mass density plot'
)
uncalb_mass_dens_plot

In [ ]:
calb_mass_dens_plot = alphaviz.plotting.plot_mass_error(
    evidence,
    'm/z',
    'Mass error [ppm]',
    'Calibrated mass density plot'
)
calb_mass_dens_plot

In [ ]:
peptide_mz_distr = alphaviz.plotting.plot_peptide_distr(
    evidence,
    'm/z',
    'Peptide m/z distribution'
)
peptide_mz_distr

In [ ]:
peptide_length_distr = alphaviz.plotting.plot_peptide_distr(
    evidence,
    'Length',
    'Peptide length distribution'
)
peptide_length_distr